In [1]:
import pandas as pd
import plotly.express as px

scaling_df = pd.read_csv("scaling.csv")
scaling_df


queue
0        100.000000
1        100.000000
2        100.839996
3        100.839996
4        100.760002
...             ...
18721  11623.250000
18722  11737.669922
18723  11364.240234
18724  11370.959961
18725  11805.000000

[18726 rows x 1 columns]

In [2]:
px.line(data_frame=scaling_df)


In [3]:
scaling_df["queue_mean_fast"] = (
    scaling_df["queue"].rolling(window=10, min_periods=1, center=False).mean()
)
scaling_df["queue_mean_slow"] = (
    scaling_df["queue"].rolling(window=200, min_periods=1, center=False).mean()
)
scaling_df


queue  queue_mean_fast  queue_mean_slow
0        100.000000       100.000000       100.000000
1        100.000000       100.000000       100.000000
2        100.839996       100.279999       100.279999
3        100.839996       100.419998       100.419998
4        100.760002       100.487999       100.487999
...             ...              ...              ...
18721  11623.250000     12278.880957     14398.051084
18722  11737.669922     12219.183984     14381.288433
18723  11364.240234     12102.006055     14362.658633
18724  11370.959961     11985.500098     14343.379883
18725  11805.000000     11909.624121     14326.271333

[18726 rows x 3 columns]

In [4]:
px.line(data_frame=scaling_df)


In [5]:
scaling_df["queue_mean_max"] = scaling_df[["queue_mean_fast", "queue_mean_slow"]].max(
    axis=1
)
scaling_df


queue  queue_mean_fast  queue_mean_slow  queue_mean_max
0        100.000000       100.000000       100.000000      100.000000
1        100.000000       100.000000       100.000000      100.000000
2        100.839996       100.279999       100.279999      100.279999
3        100.839996       100.419998       100.419998      100.419998
4        100.760002       100.487999       100.487999      100.487999
...             ...              ...              ...             ...
18721  11623.250000     12278.880957     14398.051084    14398.051084
18722  11737.669922     12219.183984     14381.288433    14381.288433
18723  11364.240234     12102.006055     14362.658633    14362.658633
18724  11370.959961     11985.500098     14343.379883    14343.379883
18725  11805.000000     11909.624121     14326.271333    14326.271333

[18726 rows x 4 columns]

In [6]:
px.line(data_frame=scaling_df[["queue", "queue_mean_max"]])


In [7]:
sustain_window = 100
scaling_df["queue_sustain"] = scaling_df["queue_mean_max"]
for i in range(1, scaling_df.shape[0]):
    first_index = max(0, i - sustain_window)
    past_indices = [x for x in range(first_index, i)]
    past_values = scaling_df["queue_mean_max"].iloc[past_indices].values
    peak_value = max(past_values)
    scaling_df["queue_sustain"].iloc[i] = peak_value
scaling_df


queue  queue_mean_fast  queue_mean_slow  queue_mean_max  \
0        100.000000       100.000000       100.000000      100.000000   
1        100.000000       100.000000       100.000000      100.000000   
2        100.839996       100.279999       100.279999      100.279999   
3        100.839996       100.419998       100.419998      100.419998   
4        100.760002       100.487999       100.487999      100.487999   
...             ...              ...              ...             ...   
18721  11623.250000     12278.880957     14398.051084    14398.051084   
18722  11737.669922     12219.183984     14381.288433    14381.288433   
18723  11364.240234     12102.006055     14362.658633    14362.658633   
18724  11370.959961     11985.500098     14343.379883    14343.379883   
18725  11805.000000     11909.624121     14326.271333    14326.271333   

       queue_sustain  
0         100.000000  
1         100.000000  
2         100.000000  
3         100.279999  
4         100.419998  
...              ...  
18721   15071.630444  
18722   15069.605093  
18723   15068.088843  
18724   15067.682642  
18725   15067.634190  

[18726 rows x 5 columns]

In [8]:
px.line(data_frame=scaling_df[["queue", "queue_sustain"]])


In [9]:
step_width = 100
win_size = 50

step_df = pd.DataFrame(
    {"queue": [0 for i in range(step_width)] + [10 for i in range(step_width)]}
)

step_df["queue_boxcar"] = (
    step_df["queue"]
    .rolling(window=win_size, win_type="boxcar", min_periods=1, center=False)
    .mean()
)
step_df["queue_triang"] = (
    step_df["queue"]
    .rolling(window=win_size, win_type="triang", min_periods=1, center=False)
    .mean()
)
step_df["queue_bh"] = (
    step_df["queue"]
    .rolling(window=win_size, win_type="blackmanharris", min_periods=1, center=False)
    .mean()
)

px.line(data_frame=step_df)


In [10]:
pulse_width = 10

step_df = pd.DataFrame(
    {
        "queue": [0 for i in range(step_width - pulse_width // 2)]
        + [10 for i in range(pulse_width)]
        + [0 for i in range(step_width - pulse_width // 2)]
    }
)

step_df["queue_boxcar"] = (
    step_df["queue"]
    .rolling(window=win_size, win_type="boxcar", min_periods=1, center=False)
    .mean()
)
step_df["queue_triang"] = (
    step_df["queue"]
    .rolling(window=win_size, win_type="triang", min_periods=1, center=False)
    .mean()
)
step_df["queue_bh"] = (
    step_df["queue"]
    .rolling(window=win_size, win_type="blackmanharris", min_periods=1, center=False)
    .mean()
)

px.line(data_frame=step_df)


In [11]:
from prophet import Prophet
from prophet.plot import plot_plotly, plot_components_plotly

ts_df = pd.read_csv(
    "https://raw.githubusercontent.com/facebook/prophet/main/examples/example_wp_log_peyton_manning.csv"
)
m = Prophet()
m.fit(ts_df)
future = m.make_future_dataframe(periods=365)
forecast = m.predict(future)
plot_plotly(m, forecast)


20:44:42 - cmdstanpy - INFO - Chain [1] start processing
20:44:42 - cmdstanpy - INFO - Chain [1] done processing
